In [1]:
import dlc_practical_prologue as prologue
import torch.nn as nn
import torch

In [24]:
class FNN2(torch.nn.Module):
    def __init__(self):
        super(FNN2, self).__init__()

        self.model = nn.Sequential(
            nn.Linear(196, 50),
            nn.ReLU(),
            nn.Linear(50,50),
            nn.ReLU(),
            nn.Linear(50, 10),
            nn.Softmax()
        )
        
        self.predictor = nn.Sequential(
            nn.Linear(20, 2),
            nn.Sigmoid()
        )
            
            
    #this takes (Batch,14,14) input im1, im2 and converts
    def forward(self, im1, im2):
        d1 = self.model(im1.view(-1, 196))
        d2 = self.model(im2.view(-1, 196))
        concatted = torch.cat([d1,d2], dim = 1)
        target = self.predictor(concatted)
        return d1,d2,target

In [27]:
# Load the data
size = 1000
train_input, train_target, train_classes, test_input, test_target, test_classes = prologue.generate_pair_sets(size)


#normalization
#check https://stats.stackexchange.com/questions/174823/
mu, std = train_input.mean(), train_input.std()
train_input, test_input = train_input.sub(mu).div(std), test_input.sub(mu).div(std)

#split the images
train_input1, train_input2 = train_input[:, 0, :, :], train_input[:, 1, :, :] 
test_input1, test_input2 = test_input[:, 0, :, :], test_input[:, 1, :, :] 

#split the number pairs
train_classes1, train_classes2 = train_classes[:, 0], train_classes[:, 1]
test_classes1, test_classes2 = test_classes[:, 0], test_classes[:, 1]

In [36]:
model = FNN2()
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.SGD(model.parameters(), lr=0.01, momentum=0.9)
batch_size = 5
nb_epochs = 500

In [29]:
def train_model(model , nb_epochs, batch_size, optimizer, criterion):
    for e in range(nb_epochs):
        for b in range(0, train_input.size(0), batch_size):

            train_1 = train_input1[b: b + batch_size]
            train_2 = train_input2[b: b + batch_size]
            
            classes_1 = train_classes1[b: b + batch_size]
            classes_2 = train_classes2[b: b + batch_size]
            
            real_targets =  train_target[b:b + batch_size]
            

            ### Predictions & Loss
            
            d1, d2, pred = model(train_1, train_2)
            # Compute the loss for the ordering prediction,
            pred_loss =  criterion(pred.view(-1, 2), real_targets)
            if d1 is not None:
                pred_loss += criterion(d1.view(-1, 10), classes_1)
                pred_loss += criterion(d2.view(-1, 10), classes_2)
                pred_loss /= 3
   
           # Display the loss
            print("epoch =", e, ", loss = ",pred_loss.item())   
            
            # Reinitialize to 0 the gradients
            model.zero_grad()
            
            # Backward pass
            pred_loss.backward()
            
            # Update
            optimizer.step()
            
  
        

In [38]:
def compute_nb_errors(model):
    # Prediction
    d1,d2,pred = model(test_input1, test_input2)
    _, indices = torch.max(pred.view(-1,2), 1) # along dim1
    
    if d1 is not None:
        _, indices1 = torch.max(d1.view(-1,10), 1)
        _, indices2 = torch.max(d2.view(-1,10), 1)
    
    acc_target = (sum(indices == test_target) / float(size) * 100).item()
    acc_d1 = (sum(indices1 == test_classes1) / float(size) * 100).item()
    acc_d2 = (sum(indices2 == test_classes2) / float(size) * 100).item()
    return (acc_target, acc_d1, acc_d2)

  

In [39]:
print((compute_nb_errors(model)))

(93.4000015258789, 89.80000305175781, 90.4000015258789)


In [37]:
train_model(model, nb_epochs,batch_size, optimizer, criterion)

epoch = 0 , loss =  1.7662954330444336
epoch = 0 , loss =  1.7596927881240845
epoch = 0 , loss =  1.7667800188064575
epoch = 0 , loss =  1.7717229127883911
epoch = 0 , loss =  1.7631152868270874
epoch = 0 , loss =  1.7666562795639038
epoch = 0 , loss =  1.76266610622406
epoch = 0 , loss =  1.7674531936645508
epoch = 0 , loss =  1.7681161165237427
epoch = 0 , loss =  1.7714864015579224
epoch = 0 , loss =  1.7717252969741821
epoch = 0 , loss =  1.757149338722229
epoch = 0 , loss =  1.7637171745300293
epoch = 0 , loss =  1.770762324333191
epoch = 0 , loss =  1.7653135061264038
epoch = 0 , loss =  1.7679328918457031
epoch = 0 , loss =  1.7698326110839844
epoch = 0 , loss =  1.763561725616455
epoch = 0 , loss =  1.770642638206482
epoch = 0 , loss =  1.7621251344680786
epoch = 0 , loss =  1.7665914297103882
epoch = 0 , loss =  1.7623499631881714
epoch = 0 , loss =  1.7676410675048828
epoch = 0 , loss =  1.7624731063842773
epoch = 0 , loss =  1.7680116891860962
epoch = 0 , loss =  1.755763173

epoch = 1 , loss =  1.7527185678482056
epoch = 1 , loss =  1.753466248512268
epoch = 1 , loss =  1.7384988069534302
epoch = 1 , loss =  1.7537832260131836
epoch = 1 , loss =  1.7443885803222656
epoch = 1 , loss =  1.7480908632278442
epoch = 1 , loss =  1.757642149925232
epoch = 1 , loss =  1.750563621520996
epoch = 1 , loss =  1.7693185806274414
epoch = 1 , loss =  1.7491501569747925
epoch = 1 , loss =  1.75200355052948
epoch = 1 , loss =  1.757367730140686
epoch = 1 , loss =  1.7553285360336304
epoch = 1 , loss =  1.7441434860229492
epoch = 1 , loss =  1.7313545942306519
epoch = 1 , loss =  1.7346820831298828
epoch = 1 , loss =  1.7572063207626343
epoch = 1 , loss =  1.7652082443237305
epoch = 1 , loss =  1.7514671087265015
epoch = 1 , loss =  1.731981635093689
epoch = 1 , loss =  1.7555623054504395
epoch = 1 , loss =  1.7425661087036133
epoch = 1 , loss =  1.7587331533432007
epoch = 1 , loss =  1.743607521057129
epoch = 1 , loss =  1.7434202432632446
epoch = 1 , loss =  1.73225319385

epoch = 2 , loss =  1.4961141347885132
epoch = 2 , loss =  1.526659607887268
epoch = 2 , loss =  1.5018366575241089
epoch = 2 , loss =  1.6152963638305664
epoch = 2 , loss =  1.6275348663330078
epoch = 2 , loss =  1.5638867616653442
epoch = 2 , loss =  1.5189499855041504
epoch = 2 , loss =  1.5634812116622925
epoch = 2 , loss =  1.5733941793441772
epoch = 2 , loss =  1.648218035697937
epoch = 2 , loss =  1.5261179208755493
epoch = 2 , loss =  1.555202603340149
epoch = 2 , loss =  1.5625038146972656
epoch = 2 , loss =  1.6265844106674194
epoch = 2 , loss =  1.5654996633529663
epoch = 2 , loss =  1.624491572380066
epoch = 2 , loss =  1.5119091272354126
epoch = 2 , loss =  1.4524726867675781
epoch = 2 , loss =  1.5029287338256836
epoch = 2 , loss =  1.5745149850845337
epoch = 2 , loss =  1.39817476272583
epoch = 2 , loss =  1.5467029809951782
epoch = 2 , loss =  1.331244945526123
epoch = 2 , loss =  1.6391388177871704
epoch = 2 , loss =  1.7553386688232422
epoch = 2 , loss =  1.6059163808

epoch = 3 , loss =  1.2667531967163086
epoch = 3 , loss =  1.4587167501449585
epoch = 3 , loss =  1.4943004846572876
epoch = 3 , loss =  1.434145450592041
epoch = 3 , loss =  1.5436248779296875
epoch = 3 , loss =  1.3596082925796509
epoch = 3 , loss =  1.3877359628677368
epoch = 3 , loss =  1.4096823930740356
epoch = 3 , loss =  1.451212763786316
epoch = 3 , loss =  1.3131295442581177
epoch = 3 , loss =  1.3240532875061035
epoch = 3 , loss =  1.371087670326233
epoch = 3 , loss =  1.2381765842437744
epoch = 3 , loss =  1.4224644899368286
epoch = 3 , loss =  1.481310248374939
epoch = 3 , loss =  1.4311517477035522
epoch = 3 , loss =  1.4370856285095215
epoch = 3 , loss =  1.5673643350601196
epoch = 3 , loss =  1.6256656646728516
epoch = 3 , loss =  1.4199355840682983
epoch = 3 , loss =  1.467559814453125
epoch = 3 , loss =  1.4992040395736694
epoch = 3 , loss =  1.4309821128845215
epoch = 3 , loss =  1.4334408044815063
epoch = 3 , loss =  1.421600341796875
epoch = 3 , loss =  1.509996891

epoch = 4 , loss =  1.4265241622924805
epoch = 4 , loss =  1.4141432046890259
epoch = 4 , loss =  1.410862922668457
epoch = 4 , loss =  1.3315752744674683
epoch = 4 , loss =  1.4974002838134766
epoch = 4 , loss =  1.3679345846176147
epoch = 4 , loss =  1.3618544340133667
epoch = 4 , loss =  1.3675457239151
epoch = 4 , loss =  1.2787359952926636
epoch = 4 , loss =  1.4463820457458496
epoch = 4 , loss =  1.479738712310791
epoch = 4 , loss =  1.2968729734420776
epoch = 4 , loss =  1.4935612678527832
epoch = 4 , loss =  1.5201791524887085
epoch = 4 , loss =  1.3102577924728394
epoch = 4 , loss =  1.3326778411865234
epoch = 4 , loss =  1.3070768117904663
epoch = 4 , loss =  1.3890291452407837
epoch = 4 , loss =  1.3872617483139038
epoch = 4 , loss =  1.3160786628723145
epoch = 4 , loss =  1.4324302673339844
epoch = 4 , loss =  1.270702838897705
epoch = 4 , loss =  1.433290958404541
epoch = 4 , loss =  1.3967443704605103
epoch = 4 , loss =  1.4054168462753296
epoch = 4 , loss =  1.3006118535

...

epoch = 495 , loss =  1.0936294794082642
epoch = 495 , loss =  1.116317629814148
epoch = 495 , loss =  1.1879150867462158
epoch = 495 , loss =  1.0888384580612183
epoch = 495 , loss =  1.0932940244674683
epoch = 495 , loss =  1.2415989637374878
epoch = 495 , loss =  1.0822547674179077
epoch = 495 , loss =  1.2132782936096191
epoch = 495 , loss =  1.090013027191162
epoch = 495 , loss =  1.096455693244934
epoch = 495 , loss =  1.1113755702972412
epoch = 495 , loss =  1.1097444295883179
epoch = 495 , loss =  1.3007363080978394
epoch = 495 , loss =  1.0825625658035278
epoch = 495 , loss =  1.0904021263122559
epoch = 495 , loss =  1.1118754148483276
epoch = 495 , loss =  1.0864278078079224
epoch = 495 , loss =  1.0860475301742554
epoch = 495 , loss =  1.08107328414917
epoch = 495 , loss =  1.0793583393096924
epoch = 495 , loss =  1.1130491495132446
epoch = 495 , loss =  1.0933865308761597
epoch = 495 , loss =  1.0980626344680786
epoch = 495 , loss =  1.0934346914291382
epoch = 495 , loss = 

epoch = 496 , loss =  1.2132759094238281
epoch = 496 , loss =  1.0899940729141235
epoch = 496 , loss =  1.0964336395263672
epoch = 496 , loss =  1.1113466024398804
epoch = 496 , loss =  1.1097270250320435
epoch = 496 , loss =  1.3007172346115112
epoch = 496 , loss =  1.082554817199707
epoch = 496 , loss =  1.090384840965271
epoch = 496 , loss =  1.1118415594100952
epoch = 496 , loss =  1.0864115953445435
epoch = 496 , loss =  1.0860313177108765
epoch = 496 , loss =  1.0810641050338745
epoch = 496 , loss =  1.0793604850769043
epoch = 496 , loss =  1.1130303144454956
epoch = 496 , loss =  1.0933648347854614
epoch = 496 , loss =  1.0980340242385864
epoch = 496 , loss =  1.0934110879898071
epoch = 496 , loss =  1.1038156747817993
epoch = 496 , loss =  1.2143157720565796
epoch = 496 , loss =  1.1513229608535767
epoch = 496 , loss =  1.1748378276824951
epoch = 496 , loss =  1.0844489336013794
epoch = 496 , loss =  1.0794535875320435
epoch = 496 , loss =  1.1025935411453247
epoch = 496 , loss

epoch = 497 , loss =  1.0860151052474976
epoch = 497 , loss =  1.0810537338256836
epoch = 497 , loss =  1.0793637037277222
epoch = 497 , loss =  1.1130120754241943
epoch = 497 , loss =  1.0933425426483154
epoch = 497 , loss =  1.0980055332183838
epoch = 497 , loss =  1.0933877229690552
epoch = 497 , loss =  1.1037918329238892
epoch = 497 , loss =  1.2143175601959229
epoch = 497 , loss =  1.1513047218322754
epoch = 497 , loss =  1.1748363971710205
epoch = 497 , loss =  1.0844365358352661
epoch = 497 , loss =  1.0794501304626465
epoch = 497 , loss =  1.1025782823562622
epoch = 497 , loss =  1.1520227193832397
epoch = 497 , loss =  1.145429253578186
epoch = 497 , loss =  1.0909937620162964
epoch = 497 , loss =  1.08333158493042
epoch = 497 , loss =  1.1128877401351929
epoch = 497 , loss =  1.1645143032073975
epoch = 497 , loss =  1.1293481588363647
epoch = 497 , loss =  1.0959852933883667
epoch = 497 , loss =  1.084715485572815
epoch = 497 , loss =  1.0987499952316284
epoch = 497 , loss =

epoch = 498 , loss =  1.2143198251724243
epoch = 498 , loss =  1.151287317276001
epoch = 498 , loss =  1.174835443496704
epoch = 498 , loss =  1.084424614906311
epoch = 498 , loss =  1.079446792602539
epoch = 498 , loss =  1.1025627851486206
epoch = 498 , loss =  1.1520127058029175
epoch = 498 , loss =  1.1453932523727417
epoch = 498 , loss =  1.0909804105758667
epoch = 498 , loss =  1.0833269357681274
epoch = 498 , loss =  1.112860083580017
epoch = 498 , loss =  1.1645017862319946
epoch = 498 , loss =  1.1293317079544067
epoch = 498 , loss =  1.095963478088379
epoch = 498 , loss =  1.084701418876648
epoch = 498 , loss =  1.0987334251403809
epoch = 498 , loss =  1.0803078413009644
epoch = 498 , loss =  1.2477457523345947
epoch = 498 , loss =  1.1089035272598267
epoch = 498 , loss =  1.1528645753860474
epoch = 498 , loss =  1.0962412357330322
epoch = 498 , loss =  1.0804170370101929
epoch = 498 , loss =  1.1175066232681274
epoch = 498 , loss =  1.0934834480285645
epoch = 498 , loss =  1

epoch = 499 , loss =  1.095941185951233
epoch = 499 , loss =  1.0846872329711914
epoch = 499 , loss =  1.0987166166305542
epoch = 499 , loss =  1.0803025960922241
epoch = 499 , loss =  1.2477216720581055
epoch = 499 , loss =  1.1088835000991821
epoch = 499 , loss =  1.1528494358062744
epoch = 499 , loss =  1.096228003501892
epoch = 499 , loss =  1.080412745475769
epoch = 499 , loss =  1.1174739599227905
epoch = 499 , loss =  1.0934723615646362
epoch = 499 , loss =  1.1372833251953125
epoch = 499 , loss =  1.0831712484359741
epoch = 499 , loss =  1.083351731300354
epoch = 499 , loss =  1.07878577709198
epoch = 499 , loss =  1.0934624671936035
epoch = 499 , loss =  1.1669517755508423
epoch = 499 , loss =  1.1735979318618774
epoch = 499 , loss =  1.0873504877090454
epoch = 499 , loss =  1.1057038307189941
epoch = 499 , loss =  1.1502704620361328
epoch = 499 , loss =  1.103529930114746
epoch = 499 , loss =  1.0949091911315918
epoch = 499 , loss =  1.0805259943008423
epoch = 499 , loss =  1